In [1]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

pd.set_option('display.max_columns', None)
pd.set_option('display.float_format', lambda x: '%.5f' % x)

# Jetson Nano Measurements

Measurements are done using the [`tegrastats`](https://docs.nvidia.com/drive/drive_os_5.1.6.1L/nvvib_docs/index.html#page/DRIVE_OS_Linux_SDK_Development_Guide/Utilities/util_tegrastats.html) tool and a custom wrapper which converts to csv output.

In [2]:
def read_csv(path):
    df = pd.read_csv(path)
    df["dt"] = df["TIME"] - df["TIME"][0] - 10
    
    return df
df = read_csv("jetson-nano-clients_10-minpower-vhf.csv")
df

TIME   RAM  SWAP  IRAM  CPU_0  CPU_1 CPU_2 CPU_3  EMC_FREQ  \
0     1648029257.71422   749     0     0     50      0   off   off         0   
1     1648029257.72400   749     0     0      0      0   off   off         0   
2     1648029257.73260   749     0     0      0      0   off   off         0   
3     1648029257.74147   749     0     0    100      0   off   off         0   
4     1648029257.75011   749     0     0    100      0   off   off         0   
...                ...   ...   ...   ...    ...    ...   ...   ...       ...   
27509 1648029553.73134  2290     0     0     50     50   off   off         8   
27510 1648029553.74219  2290     0     0      0      0   off   off         8   
27511 1648029553.75366  2290     0     0    100      0   off   off         8   
27512 1648029553.76484  2290     0     0    100      0   off   off         8   
27513 1648029553.77727  2290     0     0    100      0   off   off         8   

       GR3D_FREQ_UTIL  GR3D_FREQ_FREQ      PLL      CPU  PMIC      GPU  \
0                   0              76 39.00000 43.00000    50 43.00000   
1                   0              76 39.00000 43.00000    50 43.00000   
2                   0              76 39.00000 43.00000    50 43.00000   
3                   0              76 39.00000 43.00000    50 43.00000   
4                   0              76 39.00000 43.00000    50 43.00000   
...               ...             ...      ...      ...   ...      ...   
27509              99             230 40.50000 45.00000    50 42.50000   
27510              99             230 40.50000 45.50000    50 42.50000   
27511              99             230 40.50000 45.00000    50 42.00000   
27512              99             230 40.50000 45.00000    50 42.00000   
27513              99             230 40.50000 45.00000    50 42.00000   

            AO  thermal  APE  POM_5V_IN_CUR  POM_5V_IN_AVG  POM_5V_GPU_CUR  \
0     45.00000 43.00000   25           2111           2111               0   
1     45.00000 43.00000   25           2111           2111               0   
2     45.00000 43.00000   25           2111           2111               0   
3     45.00000 43.00000   25           2153           2121               0   
4     45.00000 43.00000   25           2153           2127               0   
...        ...      ...  ...            ...            ...             ...   
27509 46.50000 43.75000   25           3281           2934             697   
27510 46.50000 43.75000   25           3281           2934             738   
27511 46.50000 43.75000   25           3281           2934             738   
27512 46.50000 43.75000   25           3281           2934             779   
27513 46.50000 43.75000   25           3317           2934             779   

       POM_5V_GPU_AVG  POM_5V_CPU_CUR  POM_5V_CPU_AVG        dt  
0                   0             414             414 -10.00000  
1                   0             414             414  -9.99022  
2                   0             414             414  -9.98162  
3                   0             455             424  -9.97276  
4                   0             455             430  -9.96411  
...               ...             ...             ...       ...  
27509             540             492             482 286.01712  
27510             540             492             482 286.02797  
27511             540             492             482 286.03944  
27512             540             451             482 286.05062  
27513             540             450             482 286.06305  

[27514 rows x 25 columns]

### Measurements: Dynamic addition of clients (1, 5 and 10 clients) at custom low power (1000 hz sampling rate)

In [3]:
def plot_power2(df):
    fig = make_subplots(specs=[[{"secondary_y": True}]])
    fig.layout.margin = go.layout.Margin(l=10, r=10, b=10, t=10)

    fig.add_trace(go.Scatter(x=df["dt"], y=df["POM_5V_CPU_CUR"].rolling(200).mean(), name="CPU Power"))
    fig.add_trace(go.Scatter(x=df["dt"], y=df["POM_5V_GPU_CUR"].rolling(200).mean(), name="GPU Power"))
    fig.add_trace(go.Scatter(x=df["dt"], y=df["POM_5V_IN_CUR"].rolling(200).mean(), name="Total Power"))

    #fig.add_trace(go.Scatter(x=df["dt"], y=df["CPU Usage"].rolling(10).mean(), name="CPU Usage"), secondary_y=True,)
    #fig.add_trace(go.Scatter(x=df["dt"], y=df["GR3D_FREQ_UTIL"].rolling(50).mean(), name="GPU Usage"), secondary_y=True,)

    fig.add_trace(go.Scatter(x=df["dt"], y=df["GR3D_FREQ_UTIL"].rolling(500).mean(), name="GPU Utilization",
                            line = dict(color='#FFA15A', dash='dot')), secondary_y=True,)
    fig.add_trace(go.Scatter(x=df["dt"], y=(df["CPU_0"]+df["CPU_1"]).rolling(500).mean(), name="CPU Utilization",
                            line = dict(color='#19D3F3', dash='dot')), secondary_y=True,)


    fig.update_xaxes(title_text="Time (s)")
    fig.update_yaxes(title_text="Power Consumption (mW)")
    fig.update_yaxes(title_text="Utilization (%)", secondary_y=True)
    
    return fig

In [4]:
fig = plot_power2(df)
fig.add_vline(x=7, annotation_text="Start")
fig.add_vline(x=36, annotation_text="Pipeline Running")
fig.add_vline(x=120, annotation_text="Power Client 2-5")
fig.add_vline(x=180, annotation_text="Power Client 6-10")

fig.show("notebook")

In [5]:
# power consumption of 1 client
c1 = df[5000:6000]["POM_5V_IN_CUR"].mean()
# power consumption of 5 clients
c5 = df[17000:18000]["POM_5V_IN_CUR"].mean()
# power consumption of 5 clients
c10 = df[23000:24000]["POM_5V_IN_CUR"].mean()

print(f"Custom low power mode: 1 Client: {c1/1000:.3}W, 5 Clients: {c5/1000:.3}W, 10 Clients: {c10/1000:.3}W")

Custom low power mode: 1 Client: 3.18W, 5 Clients: 3.16W, 10 Clients: 3.13W
